In [1]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.preprocessing import LabelEncoder, OneHotEncoder
from feature_engine.encoding import RareLabelEncoder
from gensim.utils import simple_preprocess
from gensim.models import Word2Vec
from xgboost import XGBClassifier
from sklearn.metrics import accuracy_score
import gradio as gr
import pickle

# Reading Data
df = pd.read_excel('01.Dataset FI_06032024.xlsx', sheet_name=2)
# Small Preprocessing
MAP_TipoInformacao = {"A": "ativo", "P": "passivo"}
MAP_TipoInstrumento = {"F21": "Numerário", "F22": "Depósitos transferíveis", "F29": "Outros depósitos", "F3_P": "Títulos de dívida", "F4": "Empréstimos", "F511": "Ações cotadas", "F512": "Ações não cotadas", "F519": "Outras participações", "F521": "Unidades de Participação emitidas por FMM", "F522": "Unidades de Participação emitidas por FI, excluindo FMM", "F71": "Derivados financeiros"}
MAP_MaturidadeOriginal = {"01": "A vista", "10": "Ate 1 ano", "06": "De 1 a 2 anos", "07": "De 2 a 5 anos", "08": "A mais de 5 anos", "_Z": "Não aplicável"}
df.TipoInformacao = df.TipoInformacao.map(MAP_TipoInformacao)
df.TipoInstrumento = df.TipoInstrumento.map(MAP_TipoInstrumento)
df.MaturidadeOriginal = df.MaturidadeOriginal.map(MAP_MaturidadeOriginal)
df.drop(["CodEntidadeRef", "CodEntidadeCon"], axis=1, inplace=True)
df.head(3)
# Feature Engineering
df_clean = df.copy()
### Encoding Rare Labels
### Label Enconder
def encode_target(label, category_mapping):
  # Check if label is unseen (not in the dictionary)
  if label not in category_mapping:
    # Assign next available integer as seen in training data
    new_value = len(category_mapping)
    category_mapping[label] = new_value
  
  return category_mapping[label]
def map_numbers_to_categories(numbers, category_mapping):
    """Maps numbers back to their corresponding category names using a provided mapping dictionary.

    Args:
        numbers: A list or array containing the numerical representations of categories.
        category_mapping: A dictionary mapping category names (keys) to their numerical representations (values).

    Returns:
        A list containing the corresponding category names for the input numbers.
    """

    category_names = [category_mapping.get(number, None) for number in numbers]
    return category_names
def return_map(df_clean):

    territory_map = {}
    sector_map = {}

    # Iterate through each row (assuming TerritorioCon and encoded_label_territorio are in the same order)
    for territorio, encoded_label in zip(df_clean["TerritorioCon"], df_clean["encoded_label_territorio"]):
      # Add the mapping to the dictionary if the TerritorioCon is not already present
      if territorio not in territory_map:
        territory_map[territorio] = encoded_label
    
    for sector, encoded_label_sector in zip(df_clean["SetorInstitucionalCon"], df_clean["encoded_label_setor"]):
      # Add the mapping to the dictionary if the TerritorioCon is not already present
      if sector not in sector_map:
        sector_map[sector] = encoded_label_sector

    return territory_map, sector_map
# Get unique categories from 'TerritorioCon' column
unique_categories_ter = df_clean['TerritorioCon'].unique()
category_mapping_ter = dict(zip(unique_categories_ter, range(len(unique_categories_ter))))
inverted_mapping_ter = {value: key for key, value in category_mapping_ter.items()}

unique_categories_sec = df_clean["SetorInstitucionalCon"].unique()
category_mapping_sec = dict(zip(unique_categories_sec, range(len(unique_categories_sec))))
inverted_mapping_sec = {value: key for key, value in category_mapping_sec.items()}

df_clean["encoded_label_territorio"] = df_clean["TerritorioCon"].apply(encode_target, args=[category_mapping_ter])
df_clean["encoded_label_setor"] = df_clean['SetorInstitucionalCon'].apply(encode_target, args=[category_mapping_sec])
df_clean.head(3)
### Processing Description Column

df_clean['tokenized_Descricao_text'] = df_clean['DescricaoInstrumento'].apply(lambda x: simple_preprocess(x))
word2vec_model = Word2Vec(sentences=df_clean['tokenized_Descricao_text'], vector_size=100, window=5, min_count=1, workers=4)
df_clean
def compute_avg_embedding(tokens, unknown_embedding=[0]*word2vec_model.vector_size):
    embeddings = [word2vec_model.wv[token] for token in tokens if token in word2vec_model.wv]
    if embeddings:  # Embeddings found
        return np.array(embeddings).mean(axis=0)  # Return average embedding as a NumPy array
    else:  # No embeddings found
        return np.array(unknown_embedding)
df_clean['avg_embedding'] = df_clean['tokenized_Descricao_text'].apply(compute_avg_embedding)
X = df_clean['avg_embedding'].apply(pd.Series).to_numpy()
y1 = df_clean['encoded_label_territorio']
y2 = df_clean['encoded_label_setor']
embed_data = pd.DataFrame(X)
df_clean.head(10)

df_clean.to_csv('df_clean.csv', index=True)


C:\Users\berna\AppData\Roaming\Python\Python311\site-packages\gradio_client\documentation.py:103: UserWarning: Could not get documentation group for <class 'gradio.mix.Parallel'>: No known documentation group for module 'gradio.mix'
  warnings.warn(f"Could not get documentation group for {cls}: {exc}")
C:\Users\berna\AppData\Roaming\Python\Python311\site-packages\gradio_client\documentation.py:103: UserWarning: Could not get documentation group for <class 'gradio.mix.Series'>: No known documentation group for module 'gradio.mix'
  warnings.warn(f"Could not get documentation group for {cls}: {exc}")


In [2]:

df_clean['tokenized_Descricao_text']

0                                             [social]
1                                             [social]
2                                             [social]
3                                             [social]
4                                             [social]
                             ...                      
42402                                         [zurnvx]
42403                                         [zurnvx]
42404                                 [zuvi, nova, sa]
42405                                 [zuvi, nova, sa]
42406    [zyl, tecnologia, consultoria, inversion, sl]
Name: tokenized_Descricao_text, Length: 42407, dtype: object

In [3]:
from collections import defaultdict, Counter

tokenized_Descricao_text = df_clean['tokenized_Descricao_text']
# Dicionários para armazenar contagens de tokens para cada setor e território
setor_tokens_count = defaultdict(Counter)
territorio_tokens_count = defaultdict(Counter)

# Iterar sobre os dados e contar os tokens para cada setor e território usando apenas o primeiro token de cada descrição
for s, t, tokens in zip(df_clean['SetorInstitucionalCon'], df_clean['TerritorioCon'], tokenized_Descricao_text):
    if tokens:  # Verifique se tokens não está vazio
        first_token = tokens[0]  # Pegue o primeiro token
        setor_tokens_count[s].update([first_token])
        territorio_tokens_count[t].update([first_token])

# Exibir os tokens mais usados para cada setor
for s, token_count in setor_tokens_count.items():
    print(f"Setor: {s}")
    for token, count in token_count.most_common(5):  # Exibir os 10 tokens mais comuns
        print(f"{token}: {count}")
    print()

# Exibir os tokens mais usados para cada território
for t, token_count in territorio_tokens_count.items():
    print(f"Território: {t}")
    for token, count in token_count.most_common(5):  # Exibir os 10 tokens mais comuns
        print(f"{token}: {count}")
    print()




Setor: S127
vw: 71
hsbc: 68
bn: 60
frn: 55
bmw: 53

Setor: S11
sx: 245
pc: 190
bn: 156
spx: 156
nos: 135

Setor: S121
caixa: 19
numerário: 10
prt: 6
fii: 4
dda: 3

Setor: S126
mizuho: 55
gs: 54
aib: 51
goldman: 49
ubs: 46

Setor: S124
ishares: 841
amundi: 221
lyxor: 217
part: 168
bpi: 148

Setor: S125
european: 42
ms: 39
vw: 34
ford: 33
wt: 33

Setor: S122
prt: 1925
dp: 1092
bst: 1026
banco: 593
do: 344

Setor: S1311
btps: 425
spgb: 242
frtr: 236
dbr: 156
btf: 147

Setor: S14
emprést: 12
stephane: 7
empréstimo: 6
pedro: 4
jose: 3

Setor: S128
allianz: 26
assgen: 14
fideli: 14
alvgr: 13
assicurazioni: 11

Setor: S123
groupama: 27
amundi: 20
bnp: 5
imga: 4
new: 3

Setor: S1312
community: 15
govmad: 10
reg: 6
madrid: 5
azores: 4

Setor: S1314
cades: 2

Setor: S1313
sogrpr: 4
idfmob: 1
region: 1
sogr: 1

Território: PRT
prt: 1924
dp: 1062
bst: 1026
banco: 342
do: 342

Território: CAN
bank: 46
toronto: 25
canadian: 24
td: 16
bns: 15

Território: DEU
sx: 223
dbr: 156
deutsche: 129
bubill: 11

In [6]:
import pandas as pd
from collections import defaultdict, Counter

# Dicionários para armazenar contagens de tokens para cada setor e território
setor_tokens_count = defaultdict(Counter)
territorio_tokens_count = defaultdict(Counter)

# Iterar sobre os dados e contar os tokens para cada setor e território usando apenas o primeiro token de cada descrição
for s, t, tokens in zip(df_clean['SetorInstitucionalCon'], df_clean['TerritorioCon'], tokenized_Descricao_text):
    if tokens:  # Verifique se tokens não está vazio
        first_token = tokens[0]  # Pegue o primeiro token
        setor_tokens_count[s].update([first_token])
        territorio_tokens_count[t].update([first_token])

# Listas para armazenar os resultados
setor_results = []
territorio_results = []

# Coletar os resultados para cada setor
for s, token_count in setor_tokens_count.items():
    for token, count in token_count.most_common(10):  # Pegar os 10 tokens mais comuns
        setor_results.append((s, token, count))

# Coletar os resultados para cada território
for t, token_count in territorio_tokens_count.items():
    for token, count in token_count.most_common(10):  # Pegar os 10 tokens mais comuns
        territorio_results.append((t, token, count))

# Criar DataFrames
setor_df = pd.DataFrame(setor_results, columns=['Setor Institucional', 'Token', 'Contagem'])
territorio_df = pd.DataFrame(territorio_results, columns=['Território', 'Token', 'Contagem'])

# Exibir os DataFrames
print("DataFrame para setor:")
print(setor_df)
print()

print("DataFrame para território:")
print(territorio_df)

DataFrame para setor:
    Setor Institucional   Token  Contagem
0                  S127      vw        71
1                  S127    hsbc        68
2                  S127      bn        60
3                  S127     frn        55
4                  S127     bmw        53
..                  ...     ...       ...
114               S1314   cades         2
115               S1313  sogrpr         4
116               S1313  idfmob         1
117               S1313  region         1
118               S1313    sogr         1

[119 rows x 3 columns]

DataFrame para território:
    Território   Token  Contagem
0          PRT     prt      1924
1          PRT      dp      1062
2          PRT     bst      1026
3          PRT   banco       342
4          PRT      do       342
..         ...     ...       ...
447        LIE   slhnv         2
448        SVK  slospo         4
449        SVK  sppdis         1
450        TWN  taiwan         7
451        VEN    venz         2

[452 rows x 3 columns]


In [23]:
territorio_df

Território   Token  Contagem Descrição do território
0          PRT     prt      1924                Portugal
1          PRT      dp      1062                Portugal
2          PRT     bst      1026                Portugal
3          PRT   banco       342                Portugal
4          PRT      do       342                Portugal
..         ...     ...       ...                     ...
447        LIE   slhnv         2           Liechtenstein
448        SVK  slospo         4              Eslováquia
449        SVK  sppdis         1              Eslováquia
450        TWN  taiwan         7                  Taiwan
451        VEN    venz         2               Venezuela

[452 rows x 4 columns]

In [7]:
territorio_df
df_setor =  pd.read_excel('01.Dataset FI_06032024.xlsx', sheet_name=5)
df_setor
df_país =  pd.read_excel('01.Dataset FI_06032024.xlsx', sheet_name=6)
df_país
territorio_df = territorio_df.merge(df_país, on='Território', how='left')


territorio_df
grupo_descricao = territorio_df.groupby('Descrição do território').sum()

print(grupo_descricao)

                                   Contagem
Descrição do território                    
Alemanha                               1009
Andorra                                   1
Argentina                                11
Austrália                               103
Banco Africano de Desenvolvimento         4
...                                     ...
Turquia                                   7
Venezuela                                 2
África do Sul                            26
Áustria                                 212
Índia                                    12

[84 rows x 1 columns]


C:\Users\berna\AppData\Local\Temp\ipykernel_28428\2095211135.py:10: FutureWarning: The default value of numeric_only in DataFrameGroupBy.sum is deprecated. In a future version, numeric_only will default to False. Either specify numeric_only or select only columns which should be valid for the function.
  grupo_descricao = territorio_df.groupby('Descrição do território').sum()


In [22]:
import pandas as pd
import geopandas as gpd
import folium

# Carregar um shapefile do mundo
world = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))

merged = world.merge(territorio_df, how='left', left_on='iso_a3', right_on='Território')
# Criar um mapa folium centrado em uma localização inicial
m = folium.Map(location=[0, 0], zoom_start=2)

# Adicionar o GeoDataFrame ao mapa folium
folium.GeoJson(
    merged,
    name='geojson',
    tooltip=folium.GeoJsonTooltip(fields=['Descrição do território'])
).add_to(m)

# Função para lidar com o clique em um país
def click_handler(feature, **kwargs):
    iso_a3 = feature['iso_a3']
    top5 = territorio_df[territorio_df['Território'] == iso_a3].nlargest(5, 'Contagem')
    popup_text = f"{feature['Descrição do território']} Top 5:\n"
    if not top5.empty:
        for _, row in top5.iterrows():
            popup_text += f"{row['Token']}: {row['Contagem']}\n"
    return popup_text

# Adicionar manipuladores de eventos de clique para cada país
for _, feature in merged.iterrows():
    iso_a3 = feature['iso_a3']
    top5 = territorio_df[territorio_df['Território'] == iso_a3].nlargest(5, 'Contagem')
    if not top5.empty:
        geojson = folium.GeoJson(
            feature['geometry'],
            style_function=lambda feature: {'fillColor': '#0E7A0D', 'color': '#003300'},  # cor de preenchimento para países com tokens no top 5
            highlight_function=lambda feature: {'weight': 0},  # remove o destaque dos países
            name='geojson',
            popup=folium.Popup(click_handler(feature), max_width=400)  # aumentar a largura máxima da caixa de texto do pop-up
        )
    else:
        geojson = folium.GeoJson(
            feature['geometry'],
            style_function=lambda feature: {'fillColor': '#ffffff', 'color': '#000000'},  # remova a cor de preenchimento para países sem lista
            highlight_function=lambda feature: {'weight': 0},  # remove o destaque dos países
            name='geojson',
            popup=None  # sem caixa de texto para países sem lista
        )
    geojson.add_to(m)

# Exibir o mapa interativo
m



C:\Users\berna\AppData\Local\Temp\ipykernel_28428\3631461937.py:6: FutureWarning: The geopandas.dataset module is deprecated and will be removed in GeoPandas 1.0. You can get the original 'naturalearth_lowres' data from https://www.naturalearthdata.com/downloads/110m-cultural-vectors/.
  world = gpd.read_file(gpd.datasets.get_path('naturalearth_lowres'))


In [25]:
territorio_df
territorio_df.to_csv('territorio_df.csv', index=True)

In [10]:
setor_df



Setor Institucional   Token  Contagem
0                  S127      vw        71
1                  S127    hsbc        68
2                  S127      bn        60
3                  S127     frn        55
4                  S127     bmw        53
..                  ...     ...       ...
114               S1314   cades         2
115               S1313  sogrpr         4
116               S1313  idfmob         1
117               S1313  region         1
118               S1313    sogr         1

[119 rows x 3 columns]

In [11]:
setor_df = setor_df.merge(df_setor, on='Setor Institucional', how='left')


In [12]:
setor_df

Setor Institucional   Token  Contagem  \
0                  S127      vw        71   
1                  S127    hsbc        68   
2                  S127      bn        60   
3                  S127     frn        55   
4                  S127     bmw        53   
..                  ...     ...       ...   
114               S1314   cades         2   
115               S1313  sogrpr         4   
116               S1313  idfmob         1   
117               S1313  region         1   
118               S1313    sogr         1   

                    Descrição do Setor Institucional  
0    Instituições financeiras cativas e prestamistas  
1    Instituições financeiras cativas e prestamistas  
2    Instituições financeiras cativas e prestamistas  
3    Instituições financeiras cativas e prestamistas  
4    Instituições financeiras cativas e prestamistas  
..                                               ...  
114                       Fundos de segurança social  
115                              Administração local  
116                              Administração local  
117                              Administração local  
118                              Administração local  

[119 rows x 4 columns]

In [27]:
import pandas as pd
import ipywidgets as widgets
from IPython.display import display, clear_output

# Supondo que você já tenha o DataFrame 'setor_df' e queira criar o Top 5 para cada setor

# Função para criar o Top 5 para um determinado setor
def top5_por_setor(setor):
    top5 = setor_df[setor_df['Setor Institucional'] == setor].nlargest(5, 'Contagem')
    return top5[['Token', 'Contagem']]

# Função para atualizar a lista de Top 5 quando um novo setor é selecionado
def atualizar_top5(change):
    setor_selecionado = change['new']
    with output_top5:
        clear_output()
        top5 = top5_por_setor(setor_selecionado)
        print(f"Top 5 para {setor_selecionado} ({setor_df.loc[setor_df['Setor Institucional'] == setor_selecionado, 'Descrição do Setor Institucional'].iloc[0]}):")
        print(top5)

# Obter a lista única de setores institucionais
setores = setor_df['Setor Institucional'].unique()

# Criar o menu suspenso para selecionar o setor
menu_setor = widgets.Dropdown(
    options=setores,
    description='Selecione o setor:',
    disabled=False,
)

# Definir a função de retorno de chamada para atualizar o Top 5 quando um novo setor é selecionado
menu_setor.observe(atualizar_top5, names='value')

# Criar a área de saída para exibir o Top 5
output_top5 = widgets.Output()

display(menu_setor)
display(output_top5)



Dropdown(description='Selecione o setor:', options=('S127', 'S11', 'S121', 'S126', 'S124', 'S125', 'S122', 'S1…

Output()

In [14]:
df 

TipoInformacao       TipoInstrumento  \
0              ativo     Ações não cotadas   
1              ativo  Outras participações   
2              ativo  Outras participações   
3              ativo  Outras participações   
4              ativo  Outras participações   
...              ...                   ...   
42402          ativo     Títulos de dívida   
42403          ativo     Títulos de dívida   
42404          ativo     Ações não cotadas   
42405          ativo     Ações não cotadas   
42406          ativo     Ações não cotadas   

                             DescricaoInstrumento MaturidadeOriginal  \
0                                 _CAPITAL SOCIAL      Não aplicável   
1                                 _CAPITAL SOCIAL      Não aplicável   
2                                 _CAPITAL SOCIAL      Não aplicável   
3                                 _CAPITAL SOCIAL      Não aplicável   
4                                 _CAPITAL SOCIAL      Não aplicável   
...                                           ...                ...   
42402                         ZURNVX 3.5 16-05/46   A mais de 5 anos   
42403                         ZURNVX 3.5 16-05/46   A mais de 5 anos   
42404                                Zuvi Nova SA      Não aplicável   
42405                               Zuvi Nova, SA      Não aplicável   
42406  ZYL Tecnologia Consultoria e Inversion, SL      Não aplicável   

      SetorInstitucionalCon TerritorioCon  
0                      S127           PRT  
1                       S11           PRT  
2                       S11           PRT  
3                       S11           PRT  
4                       S11           PRT  
...                     ...           ...  
42402                  S125           NLD  
42403                  S125           NLD  
42404                   S11           PRT  
42405                   S11           PRT  
42406                   S11           ESP  

[42407 rows x 6 columns]

In [15]:
df1 = pd.read_excel('01.Dataset FI_06032024.xlsx', sheet_name=2)

In [16]:
df1

CodEntidadeRef TipoInformacao TipoInstrumento  \
0               1375              A            F512   
1               1703              A            F519   
2               1703              A            F519   
3               1703              A            F519   
4               1703              A            F519   
...              ...            ...             ...   
42402           1575              A            F3_P   
42403           1578              A            F3_P   
42404           0674              A            F512   
42405           1450              A            F512   
42406           1450              A            F512   

                             DescricaoInstrumento MaturidadeOriginal  \
0                                 _CAPITAL SOCIAL                 _Z   
1                                 _CAPITAL SOCIAL                 _Z   
2                                 _CAPITAL SOCIAL                 _Z   
3                                 _CAPITAL SOCIAL                 _Z   
4                                 _CAPITAL SOCIAL                 _Z   
...                                           ...                ...   
42402                         ZURNVX 3.5 16-05/46                 08   
42403                         ZURNVX 3.5 16-05/46                 08   
42404                                Zuvi Nova SA                 _Z   
42405                               Zuvi Nova, SA                 _Z   
42406  ZYL Tecnologia Consultoria e Inversion, SL                 _Z   

             CodEntidadeCon SetorInstitucionalCon TerritorioCon  
0                 510748090                  S127           PRT  
1                 516931326                   S11           PRT  
2                 516990071                   S11           PRT  
3                 516933710                   S11           PRT  
4                 516939386                   S11           PRT  
...                     ...                   ...           ...  
42402  724500RPEZI5VVQQWE89                  S125           NLD  
42403  724500RPEZI5VVQQWE89                  S125           NLD  
42404             508993970                   S11           PRT  
42405             508993970                   S11           PRT  
42406             B87632675                   S11           ESP  

[42407 rows x 8 columns]

In [17]:
import streamlit as st
import pandas as pd

# Supondo que você já tenha o DataFrame 'setor_df' e queira criar o Top 5 para cada setor

# Função para criar o Top 5 para um determinado setor
def top5_por_setor(setor):
    top5 = setor_df[setor_df['Setor Institucional'] == setor].nlargest(5, 'Contagem')
    return top5[['Token', 'Contagem']]


# Obter a lista única de setores institucionais
setores = setor_df['Setor Institucional'].unique()

# Criar o menu suspenso para selecionar o setor
setor_selecionado = st.selectbox('Selecione o setor:', setores)

# Exibir o Top 5 quando um novo setor é selecionado
if setor_selecionado:
    top5 = top5_por_setor(setor_selecionado)
    st.write(f"Top 5 para {setor_selecionado}:")
    st.write(top5)


2024-05-12 14:59:54.517 
  command:

    streamlit run C:\Users\berna\AppData\Roaming\Python\Python311\site-packages\ipykernel_launcher.py [ARGUMENTS]


In [18]:
setor_df

Setor Institucional   Token  Contagem  \
0                  S127      vw        71   
1                  S127    hsbc        68   
2                  S127      bn        60   
3                  S127     frn        55   
4                  S127     bmw        53   
..                  ...     ...       ...   
114               S1314   cades         2   
115               S1313  sogrpr         4   
116               S1313  idfmob         1   
117               S1313  region         1   
118               S1313    sogr         1   

                    Descrição do Setor Institucional  
0    Instituições financeiras cativas e prestamistas  
1    Instituições financeiras cativas e prestamistas  
2    Instituições financeiras cativas e prestamistas  
3    Instituições financeiras cativas e prestamistas  
4    Instituições financeiras cativas e prestamistas  
..                                               ...  
114                       Fundos de segurança social  
115                              Administração local  
116                              Administração local  
117                              Administração local  
118                              Administração local  

[119 rows x 4 columns]

In [19]:
import pandas as pd
import ipywidgets as widgets
from IPython.display import display, clear_output

# Supondo que você já tenha o DataFrame 'setor_df' e queira criar o Top 5 para cada setor

# Função para criar o Top 5 para um determinado setor
def top5_por_setor(setor):
    top5 = setor_df[setor_df['Setor Institucional'] == setor].nlargest(5, 'Contagem')
    return top5[['Token', 'Contagem']]

# Função para atualizar a lista de Top 5 quando um novo setor é selecionado
def atualizar_top5(change):
    setor_selecionado = change['new']
    with output_top5:
        clear_output()
        top5 = top5_por_setor(setor_selecionado)
        print(f"Top 5 para {setor_selecionado} ({setor_df.loc[setor_df['Setor Institucional'] == setor_selecionado, 'Descrição do Setor Institucional'].iloc[0]}):")
        display(top5)

# Obter a lista única de setores institucionais
setores = setor_df['Setor Institucional'].unique()

# Criar o menu suspenso para selecionar o setor
menu_setor = widgets.Dropdown(
    options=setores,
    description='Selecione o setor:',
    disabled=False,
    style={'description_width': 'initial', 'width': '300px'}  # Adicionando estilo para melhor aparência
)

# Definir a função de retorno de chamada para atualizar o Top 5 quando um novo setor é selecionado
menu_setor.observe(atualizar_top5, names='value')

# Criar a área de saída para exibir o Top 5
output_top5 = widgets.Output(
    layout={'border': '1px solid #ccc', 'padding': '10px', 'margin-top': '10px'}  # Estilo para a área de saída
)

# Organizar widgets em um layout mais moderno
input_container = widgets.VBox([menu_setor, output_top5])

display(input_container)




In [26]:
setor_df.to_csv('setor_df.csv', index=True)

